In [1]:
# Imports / Configs / Global vars

# Import of native python tools
import os

# Visualization libraries
# import plotly.express as px

# Logging configuraiton
import logging
logging.basicConfig(format='[ %(asctime)s ][ %(levelname)s ]: %(message)s', datefmt='%m/%d/%Y %I:%M:%S %p')
logger = logging.getLogger()
logger.setLevel(logging.INFO)


# Ipython configs
from IPython.core.display import display, HTML
from IPython.core.interactiveshell import InteractiveShell
display(HTML("<style>.container { width:90% !important; }</style>"))
InteractiveShell.ast_node_interactivity = 'all'

# Pandas configs
import pandas as pd
pd.options.display.max_rows = 350
pd.options.display.max_columns = 250
import plotly.express as px
from plotly.offline import init_notebook_mode, iplot

init_notebook_mode(connected=True)

# Jupyter configs
%load_ext autoreload
%autoreload 2
%config Completer.use_jedi = False

/var/folders/0b/hbv1x9fd5f37yqz3mxj52y5r0000gq/T/ipykernel_14647/1337180755.py:17: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


# Data

In [2]:
df = pd.read_csv('../data/03_primary/dataset.csv')
df = df.sort_values('date').reset_index(drop=True)
df.loc[:, 'AED': 'UZS'] = df.loc[:, 'AED': 'UZS'].fillna(method='bfill')

In [3]:
def split_X_y(df: pd.DataFrame):
    X = df.loc[:, 'AED':]
    y = df[['calculated_cost']]
    return X, y

X, y = split_X_y(df)

In [4]:
pd.concat([X, y], axis=1).corr()

AED       CAD       CHF       CNY       CZK   
AED                      1.000000  0.131773  0.295577  0.211806  0.340502  \
CAD                      0.131773  1.000000  0.110380  0.424163  0.130077   
CHF                      0.295577  0.110380  1.000000  0.750320  0.371052   
CNY                      0.211806  0.424163  0.750320  1.000000  0.261831   
CZK                      0.340502  0.130077  0.371052  0.261831  1.000000   
EUR                      0.128853  0.097864  0.854327  0.614317  0.310612   
GBP                      0.128112  0.262841  0.767112  0.719641  0.109867   
GEL                      0.280118 -0.107055 -0.050042 -0.183054  0.330395   
HKD                      0.608209  0.276298  0.472563  0.526456  0.558787   
ILS                      0.274784  0.455913  0.023135  0.081329  0.328217   
INR                      0.274572  0.450400  0.284875  0.347932  0.506234   
JPY                     -0.040879  0.609710  0.209317  0.508988  0.262215   
KGS                      0.381334  0.084757  0.079139  0.101650 -0.259925   
KRW                      0.177563 -0.033730  0.303261  0.228904 -0.220822   
MYR                      0.485018  0.385353  0.523741  0.618391  0.604358   
PLN                      0.304511  0.300829  0.394304  0.565033  0.307471   
RUB                      0.105544 -0.236440 -0.369699 -0.431321 -0.584601   
THB                      0.208544 -0.287445  0.060755 -0.254776  0.526752   
TRY                      0.002429  0.343653  0.176594  0.368560 -0.233966   
UAH                     -0.173955  0.124205 -0.125333 -0.006089 -0.542212   
USD                      0.439239  0.007624  0.603177  0.336904 -0.049618   
UZS                      0.399677  0.074886  0.275960  0.285496  0.545499   
price_per_barrel        -0.100208  0.384095 -0.006676  0.360655 -0.327475   
price_per_barrel_open   -0.100213  0.385814  0.031951  0.374638 -0.317020   
price_per_barrel_max    -0.090375  0.395706  0.049346  0.391117 -0.317579   
price_per_barrel_min    -0.108692  0.379633 -0.030562  0.339901 -0.336024   
price_per_barrel_volume -0.233734  0.112200  0.045303 -0.006219  0.040727   
relative_diff_lag_1     -0.007268 -0.007310 -0.125968 -0.048150 -0.016541   
calculated_cost          0.007977  0.022581  0.054486  0.048430  0.032863   

                              EUR       GBP       GEL       HKD       ILS   
AED                      0.128853  0.128112  0.280118  0.608209  0.274784  \
CAD                      0.097864  0.262841 -0.107055  0.276298  0.455913   
CHF                      0.854327  0.767112 -0.050042  0.472563  0.023135   
CNY                      0.614317  0.719641 -0.183054  0.526456  0.081329   
CZK                      0.310612  0.109867  0.330395  0.558787  0.328217   
EUR                      1.000000  0.855811 -0.089445  0.320382 -0.001486   
GBP                      0.855811  1.000000 -0.141994  0.355702 -0.040301   
GEL                     -0.089445 -0.141994  1.000000  0.064080  0.329081   
HKD                      0.320382  0.355702  0.064080  1.000000  0.266436   
ILS                     -0.001486 -0.040301  0.329081  0.266436  1.000000   
INR                      0.315601  0.257778 -0.226791  0.454200  0.218878   
JPY                      0.234315  0.349470 -0.245740  0.345219  0.321139   
KGS                      0.070252  0.264932  0.161583  0.176087 -0.007960   
KRW                      0.279399  0.390556 -0.357825  0.128740 -0.277050   
MYR                      0.386812  0.462808 -0.067421  0.853511  0.206763   
PLN                      0.280800  0.472919 -0.109739  0.676406  0.087984   
RUB                     -0.464210 -0.387024  0.070461 -0.313110 -0.176737   
THB                      0.170172 -0.030544  0.503263 -0.026836  0.156843   
TRY                      0.249245  0.507243 -0.435441  0.089522 -0.042308   
UAH                      0.022048  0.237015 -0.439411 -0.053871 -0.207974   
USD                      0.458037  0.446131  0.124160  0.237182 -0.006865   
UZS                      

# Main
1. Correlation analysis MLR
1. LightGBM: importance estimate on a single day
1. LightGBM: importance estimate on a week & month


### LightGBM

In [5]:
import lightgbm
from sklearn.model_selection import train_test_split

In [6]:
# GridSearchCV :: lightgbm
from sklearn.model_selection import GridSearchCV
import lightgbm as lgb

#Define the parameters
parameters = {
    'n_estimators': [1, 20, 100],
    'num_leaves':[20,40,60,80,100],
    'min_child_samples':[5,10,15],
    'max_depth':[-1,5,10,20],
    'learning_rate':[0.05,0.1,0.2],
    'reg_lambda':[0,0.01,0.03],
    'importance_type': ['gain'],
}

#Define the scoring
clf = GridSearchCV(
    estimator=lgb.LGBMRegressor(),
    param_grid=parameters,
    refit='neg_mean_squared_error',
    scoring=[
        'neg_mean_squared_log_error',
        'neg_median_absolute_error',
        'neg_mean_squared_error',
        'r2',
    ],
    cv=5,
    verbose=4,
    n_jobs=-1,
)


clf = clf.fit(X=X, y=y)
cv = pd.DataFrame(clf.cv_results_)
cv.to_csv('../data/04_feature/lightgbm_baseline_dataset_score_table.csv', index=False)

# Estimation of feature importance :: lightgbm
gbt = clf.estimator
gbt.fit(X=X, y=y)
pd.DataFrame([list(gbt.feature_importances_)], columns=X.columns, index=[0]).to_csv('../data/04_feature/lightgbm_importance_table.csv', index=False)

Fitting 5 folds for each of 1620 candidates, totalling 8100 fits
[CV 1/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0.01; neg_mean_squared_error: (test=-1974980636.619) neg_mean_squared_log_error: (test=-5.880) neg_median_absolute_error: (test=-30028.836) r2: (test=-0.017) total time=   0.0s
[CV 1/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=40, reg_lambda=0.01; neg_mean_squared_error: (test=-1975347326.670) neg_mean_squared_log_error: (test=-5.879) neg_median_absolute_error: (test=-29984.910) r2: (test=-0.017) total time=   0.1s
[CV 1/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=60, reg_lambda=0; neg_mean_squared_error: (test=-1975361149.108) neg_mean_squared_log_error: (test=-5.879) neg_median_absolute_error: (test=-29968.806) r2: (test=-0.017) total time=   0.0s
[CV 5/5] EN

[CV 1/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0; neg_mean_squared_error: (test=-1974982073.317) neg_mean_squared_log_error: (test=-5.880) neg_median_absolute_error: (test=-30028.836) r2: (test=-0.017) total time=   0.1s
[CV 4/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0.01; neg_mean_squared_error: (test=-1332844225.622) neg_mean_squared_log_error: (test=-4.496) neg_median_absolute_error: (test=-26451.348) r2: (test=-0.002) total time=   0.0s
[CV 3/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0.03; neg_mean_squared_error: (test=-1245367114.969) neg_mean_squared_log_error: (test=-4.545) neg_median_absolute_error: (test=-26023.139) r2: (test=-0.003) total time=   0.0s
[CV 4/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_chi

[CV 4/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0; neg_mean_squared_error: (test=-1332844240.763) neg_mean_squared_log_error: (test=-4.496) neg_median_absolute_error: (test=-26451.348) r2: (test=-0.002) total time=   0.0s
[CV 1/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0.03; neg_mean_squared_error: (test=-1974977767.192) neg_mean_squared_log_error: (test=-5.880) neg_median_absolute_error: (test=-30028.835) r2: (test=-0.017) total time=   0.0s
[CV 5/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0.03; neg_mean_squared_error: (test=-1411058197.298) neg_mean_squared_log_error: (test=-3.463) neg_median_absolute_error: (test=-25491.062) r2: (test=-0.000) total time=   0.0s
[CV 2/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_chi

[CV 3/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0.01; neg_mean_squared_error: (test=-1245367111.844) neg_mean_squared_log_error: (test=-4.545) neg_median_absolute_error: (test=-26023.139) r2: (test=-0.003) total time=   0.0s
[CV 3/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=40, reg_lambda=0.01; neg_mean_squared_error: (test=-1245411104.430) neg_mean_squared_log_error: (test=-4.545) neg_median_absolute_error: (test=-26038.078) r2: (test=-0.003) total time=   0.0s
[CV 4/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=40, reg_lambda=0.03; neg_mean_squared_error: (test=-1332864778.454) neg_mean_squared_log_error: (test=-4.496) neg_median_absolute_error: (test=-26491.156) r2: (test=-0.002) total time=   0.0s
[CV 3/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_

[CV 2/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0; neg_mean_squared_error: (test=-1299549022.628) neg_mean_squared_log_error: (test=-4.927) neg_median_absolute_error: (test=-28451.366) r2: (test=-0.005) total time=   0.0s
[CV 5/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=20, reg_lambda=0.01; neg_mean_squared_error: (test=-1411058270.788) neg_mean_squared_log_error: (test=-3.463) neg_median_absolute_error: (test=-25491.061) r2: (test=-0.000) total time=   0.1s
[CV 2/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_samples=5, n_estimators=1, num_leaves=40, reg_lambda=0; neg_mean_squared_error: (test=-1299643474.638) neg_mean_squared_log_error: (test=-4.927) neg_median_absolute_error: (test=-28423.467) r2: (test=-0.005) total time=   0.0s
[CV 1/5] END importance_type=gain, learning_rate=0.05, max_depth=-1, min_child_

...

[CV 4/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=20, num_leaves=60, reg_lambda=0.01; neg_mean_squared_error: (test=-1350300449.145) neg_mean_squared_log_error: (test=-4.430) neg_median_absolute_error: (test=-25548.846) r2: (test=-0.015) total time=   0.1s
[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=20, num_leaves=60, reg_lambda=0.01; neg_mean_squared_error: (test=-1485480744.300) neg_mean_squared_log_error: (test=-3.337) neg_median_absolute_error: (test=-23787.558) r2: (test=-0.053) total time=   0.1s
[CV 1/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=20, num_leaves=60, reg_lambda=0.03; neg_mean_squared_error: (test=-2109992129.199) neg_mean_squared_log_error: (test=-5.783) neg_median_absolute_error: (test=-29040.624) r2: (test=-0.087) total time=   0.1s
[CV 1/5] END importance_type=gain, learning_rate=0.2, max_depth=10, mi

[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=5, n_estimators=20, num_leaves=60, reg_lambda=0.03; neg_mean_squared_error: (test=-1485831919.763) neg_mean_squared_log_error: (test=-3.323) neg_median_absolute_error: (test=-23455.492) r2: (test=-0.053) total time=   0.1s
[CV 1/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=5, n_estimators=20, num_leaves=80, reg_lambda=0; neg_mean_squared_error: (test=-2111945800.677) neg_mean_squared_log_error: (test=-5.808) neg_median_absolute_error: (test=-29289.184) r2: (test=-0.088) total time=   0.1s
[CV 2/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=5, n_estimators=20, num_leaves=80, reg_lambda=0; neg_mean_squared_error: (test=-1421047200.118) neg_mean_squared_log_error: (test=-4.654) neg_median_absolute_error: (test=-25748.542) r2: (test=-0.099) total time=   0.1s
[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_s

[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=20, num_leaves=60, reg_lambda=0.03; neg_mean_squared_error: (test=-1244847413.718) neg_mean_squared_log_error: (test=-4.419) neg_median_absolute_error: (test=-24778.947) r2: (test=-0.003) total time=   0.1s
[CV 4/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=20, num_leaves=60, reg_lambda=0.03; neg_mean_squared_error: (test=-1349967195.374) neg_mean_squared_log_error: (test=-4.431) neg_median_absolute_error: (test=-25528.351) r2: (test=-0.014) total time=   0.1s
[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=20, num_leaves=60, reg_lambda=0.03; neg_mean_squared_error: (test=-1484610836.189) neg_mean_squared_log_error: (test=-3.339) neg_median_absolute_error: (test=-23853.665) r2: (test=-0.052) total time=   0.1s
[CV 4/5] END importance_type=gain, learning_rate=0.2, max_depth=10, mi

[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=20, num_leaves=80, reg_lambda=0; neg_mean_squared_error: (test=-1491402602.697) neg_mean_squared_log_error: (test=-3.336) neg_median_absolute_error: (test=-24312.175) r2: (test=-0.057) total time=   0.1s
[CV 1/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=20, num_leaves=80, reg_lambda=0.01; neg_mean_squared_error: (test=-2117676841.526) neg_mean_squared_log_error: (test=-5.799) neg_median_absolute_error: (test=-29383.805) r2: (test=-0.091) total time=   0.1s
[CV 2/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=20, num_leaves=80, reg_lambda=0.01; neg_mean_squared_error: (test=-1414966876.441) neg_mean_squared_log_error: (test=-4.648) neg_median_absolute_error: (test=-25671.750) r2: (test=-0.095) total time=   0.1s
[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_c

LGBMRegressor()

## Modeling on lag aggregated data
for 7 days & 30 days

In [7]:
df = pd.read_csv('../data/03_primary/dataset_with_lag_aggregates.csv')
X, y = split_X_y(df)

clf = clf.fit(X=X, y=y)
cv = pd.DataFrame(clf.cv_results_)
cv.to_csv('../data/04_feature/lightgbm_lag_aggs_dataset_score_table.csv', index=False)

# Estimation of feature importance :: lightgbm
gbt = clf.estimator
gbt.fit(X=X, y=y)
pd.DataFrame([list(gbt.feature_importances_)], columns=X.columns, index=[0]).to_csv('../data/04_feature/lightgbm_params_on_lag_aggs.csv', index=False)

Fitting 5 folds for each of 1620 candidates, totalling 8100 fits
[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=10, n_estimators=1, num_leaves=20, reg_lambda=0.03; neg_mean_squared_error: (test=-1244412638.706) neg_mean_squared_log_error: (test=-4.529) neg_median_absolute_error: (test=-25833.325) r2: (test=-0.002) total time=   0.0s
[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=10, n_estimators=1, num_leaves=40, reg_lambda=0; neg_mean_squared_error: (test=-1244595248.039) neg_mean_squared_log_error: (test=-4.531) neg_median_absolute_error: (test=-25820.586) r2: (test=-0.002) total time=   0.0s
[CV 2/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=10, n_estimators=1, num_leaves=40, reg_lambda=0.03; neg_mean_squared_error: (test=-1300583013.942) neg_mean_squared_log_error: (test=-4.873) neg_median_absolute_error: (test=-27336.990) r2: (test=-0.006) total time=   0.0s
[CV 4/5] EN

/Users/adil.rashitov/Library/Caches/pypoetry/virtualenvs/research-master-paper-Nu4RI9XT-py3.11/lib/python3.11/site-packages/joblib/externals/loky/process_executor.py:700: UserWarning:

A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.



[CV 1/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=10, n_estimators=1, num_leaves=80, reg_lambda=0; neg_mean_squared_error: (test=-1986010499.671) neg_mean_squared_log_error: (test=-5.866) neg_median_absolute_error: (test=-30224.772) r2: (test=-0.023) total time=   0.0s
[CV 1/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=10, n_estimators=1, num_leaves=100, reg_lambda=0; neg_mean_squared_error: (test=-1985731091.771) neg_mean_squared_log_error: (test=-5.869) neg_median_absolute_error: (test=-30224.772) r2: (test=-0.023) total time=   0.0s
[CV 2/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=10, n_estimators=1, num_leaves=100, reg_lambda=0; neg_mean_squared_error: (test=-1301029130.250) neg_mean_squared_log_error: (test=-4.876) neg_median_absolute_error: (test=-27458.766) r2: (test=-0.006) total time=   0.1s
[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_sa

[CV 4/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=15, n_estimators=1, num_leaves=20, reg_lambda=0.01; neg_mean_squared_error: (test=-1333725480.838) neg_mean_squared_log_error: (test=-4.483) neg_median_absolute_error: (test=-26296.364) r2: (test=-0.002) total time=   0.0s
[CV 4/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=15, n_estimators=1, num_leaves=20, reg_lambda=0.03; neg_mean_squared_error: (test=-1333723316.375) neg_mean_squared_log_error: (test=-4.483) neg_median_absolute_error: (test=-26296.389) r2: (test=-0.002) total time=   0.0s
[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=15, n_estimators=1, num_leaves=20, reg_lambda=0.03; neg_mean_squared_error: (test=-1412618719.916) neg_mean_squared_log_error: (test=-3.444) neg_median_absolute_error: (test=-25337.047) r2: (test=-0.001) total time=   0.0s
[CV 1/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_c

[CV 2/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=10, n_estimators=20, num_leaves=60, reg_lambda=0; neg_mean_squared_error: (test=-1409564802.618) neg_mean_squared_log_error: (test=-4.649) neg_median_absolute_error: (test=-25562.635) r2: (test=-0.090) total time=   0.1s
[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=10, n_estimators=20, num_leaves=60, reg_lambda=0; neg_mean_squared_error: (test=-1242049965.989) neg_mean_squared_log_error: (test=-4.459) neg_median_absolute_error: (test=-24793.246) r2: (test=-0.000) total time=   0.1s
[CV 4/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_samples=10, n_estimators=20, num_leaves=60, reg_lambda=0; neg_mean_squared_error: (test=-1368137477.203) neg_mean_squared_log_error: (test=-4.427) neg_median_absolute_error: (test=-25849.843) r2: (test=-0.028) total time=   0.1s
[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=20, min_child_s

...

[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=10, n_estimators=20, num_leaves=80, reg_lambda=0.03; neg_mean_squared_error: (test=-1721880139.079) neg_mean_squared_log_error: (test=-3.328) neg_median_absolute_error: (test=-25272.378) r2: (test=0.007) total time=   0.8s
[CV 4/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=10, n_estimators=20, num_leaves=100, reg_lambda=0.01; neg_mean_squared_error: (test=-2018567077.453) neg_mean_squared_log_error: (test=-2.679) neg_median_absolute_error: (test=-25757.902) r2: (test=-0.112) total time=   0.9s
[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=10, n_estimators=20, num_leaves=100, reg_lambda=0.03; neg_mean_squared_error: (test=-1180726835.265) neg_mean_squared_log_error: (test=-4.573) neg_median_absolute_error: (test=-27196.093) r2: (test=-0.081) total time=   0.8s
[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=10, m

[CV 1/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=10, n_estimators=20, num_leaves=80, reg_lambda=0; neg_mean_squared_error: (test=-1315751267.824) neg_mean_squared_log_error: (test=-4.028) neg_median_absolute_error: (test=-29345.171) r2: (test=-0.022) total time=   0.9s
[CV 2/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=10, n_estimators=20, num_leaves=80, reg_lambda=0.03; neg_mean_squared_error: (test=-1160719700.980) neg_mean_squared_log_error: (test=-8.750) neg_median_absolute_error: (test=-28117.219) r2: (test=-0.150) total time=   0.8s
[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=10, n_estimators=20, num_leaves=100, reg_lambda=0; neg_mean_squared_error: (test=-1721877488.974) neg_mean_squared_log_error: (test=-3.328) neg_median_absolute_error: (test=-25280.171) r2: (test=0.007) total time=   1.0s
[CV 1/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_chil

[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=10, n_estimators=20, num_leaves=100, reg_lambda=0.01; neg_mean_squared_error: (test=-1180726711.949) neg_mean_squared_log_error: (test=-4.573) neg_median_absolute_error: (test=-27193.161) r2: (test=-0.081) total time=   1.1s
[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=10, n_estimators=100, num_leaves=20, reg_lambda=0.01; neg_mean_squared_error: (test=-1722020113.435) neg_mean_squared_log_error: (test=-3.327) neg_median_absolute_error: (test=-25280.804) r2: (test=0.007) total time=   1.4s
[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=10, n_estimators=100, num_leaves=20, reg_lambda=0.03; neg_mean_squared_error: (test=-1181557230.854) neg_mean_squared_log_error: (test=-4.573) neg_median_absolute_error: (test=-27162.370) r2: (test=-0.081) total time=   1.4s
[CV 3/5] END importance_type=gain, learning_rate=0.2, max_depth=10, 

[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=1, num_leaves=80, reg_lambda=0.03; neg_mean_squared_error: (test=-1146781390.451) neg_mean_squared_log_error: (test=-4.600) neg_median_absolute_error: (test=-27059.369) r2: (test=-0.049) total time=   0.5s
[CV 5/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=1, num_leaves=100, reg_lambda=0.01; neg_mean_squared_error: (test=-1146795289.825) neg_mean_squared_log_error: (test=-4.600) neg_median_absolute_error: (test=-27059.431) r2: (test=-0.050) total time=   0.5s
[CV 4/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min_child_samples=15, n_estimators=1, num_leaves=100, reg_lambda=0.03; neg_mean_squared_error: (test=-2049282875.028) neg_mean_squared_log_error: (test=-2.711) neg_median_absolute_error: (test=-25941.125) r2: (test=-0.129) total time=   0.4s
[CV 2/5] END importance_type=gain, learning_rate=0.2, max_depth=10, min

LGBMRegressor()